# Enzyme steady-state flux
Quasi-steady state solutions of enzyme states from transition rates.

In [1]:
using Symbolics
using Groebner

## SOD model
Based on the `McAdam, 1977` model

In [2]:
@variables k1 k3 k5 EA EB EC sox

eqs = let
    vAB = k1 * sox * EA - k1 * sox * EB
    vBC = k3 * sox * EB
    vCA = k5 * EC
    dA = -vAB + vCA
    dB = vAB - vBC
    [dA, dB, EA + EB + EC - 1]
end

@time sol = Symbolics.symbolic_solve(eqs, [EA, EB, EC])[1]

 16.498778 seconds (57.58 M allocations: 2.830 GiB, 3.78% gc time, 99.59% compilation time: 3% of which was recompilation)


Dict{Symbolics.Num, Any} with 3 entries:
  EA => (k1*k5 + k3*k5) / (2k1*k5 + k3*k5 + k1*k3*sox)
  EB => (k1*k5) / (2k1*k5 + k3*k5 + k1*k3*sox)
  EC => (k1*k3*sox) / (2k1*k5 + k3*k5 + k1*k3*sox)

Superoxide consumption rate

In [3]:
vSOD = sox * (k1 * (sol[EA] + sol[EB]) + k3 * sol[EB])

simplify(vSOD)

(((2//1)*(k1^2)*k5 + (2//1)*k1*k3*k5)*sox) / (2k1*k5 + k3*k5 + k1*k3*sox)

## Complex I Gauthier model

In [4]:
@variables a12 a21 a65 a56 a61 a16 a23 a32 a34 a43 a47 a74 a57 a75 a42 a24
@variables I1 I2 I3 I4 I5 I6 I7

eqs = let
    v12 = I1 * a12 - I2 * a21
    v23 = I2 * a23 - I3 * a32
    v34 = I3 * a34 - I4 * a43
    v47 = I4 * a47 - I7 * a74
    v75 = I7 * a75 - I5 * a57
    v56 = I5 * a56 - I6 * a65
    v61 = I6 * a61 - I1 * a16
    v42 = I4 * a42 - I2 * a24
    d1 = -v12 + v61
    d2 = v12 - v23 + v42
    d3 = v23 - v34
    d4 = v34 - v47 - v42
    d5 = v75 - v56
    d6 = v56 - v61
    d7 = v47 - v75
    @assert isequal(d1 + d2 + d3 + d4 + d5 + d6 + d7, 0)
    [d1, d2, d3, d4, d5, d6, I1 + I2 + I3 + I4 + I5 + I6 + I7 - 1]
end

@time sol = Symbolics.symbolic_solve(eqs, [I1, I2, I3, I4, I5, I6, I7])[1]

 18.017649 seconds (389.52 M allocations: 13.303 GiB, 8.55% gc time, 11.72% compilation time)


Dict{Symbolics.Num, Any} with 7 entries:
  I4 => (a12*a23*a34*a56*a61*a74 + a12*a23*a34*a56*a61*a75 + a12*a23*a34*a57*a6…
  I1 => (a21*a32*a42*a56*a61*a74 + a21*a32*a42*a56*a61*a75 + a21*a32*a42*a57*a6…
  I6 => (a12*a23*a34*a47*a56*a75 + a12*a24*a32*a47*a56*a75 + a12*a24*a34*a47*a5…
  I3 => (a12*a23*a42*a56*a61*a74 + a12*a23*a42*a56*a61*a75 + a12*a23*a42*a57*a6…
  I5 => (a12*a23*a34*a47*a61*a75 + a12*a23*a34*a47*a65*a75 + a12*a24*a32*a47*a6…
  I7 => (a12*a23*a34*a47*a56*a61 + a12*a23*a34*a47*a57*a61 + a12*a23*a34*a47*a5…
  I2 => (a12*a32*a42*a56*a61*a74 + a12*a32*a42*a56*a61*a75 + a12*a32*a42*a57*a6…

Weights of all 7 states

In [5]:
for k in (I1, I2, I3, I4, I5, I6, I7)
    println(k, " = ", numerator(sol[k]))
end

I1 = a21*a32*a42*a56*a61*a74 + a21*a32*a42*a56*a61*a75 + a21*a32*a42*a57*a61*a74 + a21*a32*a42*a57*a65*a74 + a21*a32*a43*a56*a61*a74 + a21*a32*a43*a56*a61*a75 + a21*a32*a43*a57*a61*a74 + a21*a32*a43*a57*a65*a74 + a21*a32*a47*a56*a61*a75 + a21*a34*a42*a56*a61*a74 + a21*a34*a42*a56*a61*a75 + a21*a34*a42*a57*a61*a74 + a21*a34*a42*a57*a65*a74 + a21*a34*a47*a56*a61*a75 + a23*a34*a47*a56*a61*a75 + a24*a32*a47*a56*a61*a75 + a24*a34*a47*a56*a61*a75
I2 = a12*a32*a42*a56*a61*a74 + a12*a32*a42*a56*a61*a75 + a12*a32*a42*a57*a61*a74 + a12*a32*a42*a57*a65*a74 + a12*a32*a43*a56*a61*a74 + a12*a32*a43*a56*a61*a75 + a12*a32*a43*a57*a61*a74 + a12*a32*a43*a57*a65*a74 + a12*a32*a47*a56*a61*a75 + a12*a34*a42*a56*a61*a74 + a12*a34*a42*a56*a61*a75 + a12*a34*a42*a57*a61*a74 + a12*a34*a42*a57*a65*a74 + a12*a34*a47*a56*a61*a75 + a16*a32*a42*a57*a65*a74 + a16*a32*a43*a57*a65*a74 + a16*a34*a42*a57*a65*a74
I3 = a12*a23*a42*a56*a61*a74 + a12*a23*a42*a56*a61*a75 + a12*a23*a42*a57*a61*a74 + a12*a23*a42*a57*a65*a74 + a

## Complex I simplified Markevich model

In [6]:
@variables b12 b21 b23 b32 b34 b43 b41 b14
@variables C1 C1_Q C1_SQ C1_QH2

eqs = let
    v12 = C1 * b12 - C1_Q * b21
    v23 = C1_Q * b23 - C1_SQ * b32
    v34 = C1_SQ * b34 - C1_QH2 * b43
    v41 = C1_QH2 * b41 - C1 * b14

    d1 = -v12 + v41
    d2 = v12 - v23
    d3 = v23 - v34
    d4 = v34 - v41

    @assert isequal(sum([d1, d2, d3, d4]), 0)

    [d1, d2, d3, d4, sum([C1, C1_Q, C1_SQ, C1_QH2]) - 1]
end

@time sol = Symbolics.symbolic_solve(eqs, [C1, C1_Q, C1_SQ, C1_QH2])[1]

  0.800344 seconds (4.87 M allocations: 209.721 MiB, 3.24% gc time, 77.64% compilation time)


Dict{Symbolics.Num, Any} with 4 entries:
  C1_QH2 => (b12*b23*b34 + b14*b21*b32 + b14*b21*b34 + b14*b23*b34) / (b12*b23*…
  C1_SQ  => (b12*b23*b41 + b12*b23*b43 + b14*b21*b43 + b14*b23*b43) / (b12*b23*…
  C1_Q   => (b12*b32*b41 + b12*b32*b43 + b12*b34*b41 + b14*b32*b43) / (b12*b23*…
  C1     => (b21*b32*b41 + b21*b32*b43 + b21*b34*b41 + b23*b34*b41) / (b12*b23*…

Weights of all 7 states

In [7]:
for k in [C1, C1_Q, C1_SQ, C1_QH2]
    println(k, " = ", numerator(sol[k]))
end

C1 = b21*b32*b41 + b21*b32*b43 + b21*b34*b41 + b23*b34*b41
C1_Q = b12*b32*b41 + b12*b32*b43 + b12*b34*b41 + b14*b32*b43
C1_SQ = b12*b23*b41 + b12*b23*b43 + b14*b21*b43 + b14*b23*b43
C1_QH2 = b12*b23*b34 + b14*b21*b32 + b14*b21*b34 + b14*b23*b34


---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*